In [1]:
import numpy as np
import scipy.stats as stats
from tqdm import tnrange, tqdm_notebook

from allensdk.core.brain_observatory_cache import BrainObservatoryCache

#Plotting tools
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
from plotly.graph_objs import Scatter, Figure, Layout,Bar

from force import NeuralNetwork
from force import Simulation


init_notebook_mode(connected=True)

In [3]:
#boc = BrainObservatoryCache(manifest_file='/Users/elijahc/dev/allen-assistant/boc/manifest.json')
boc = BrainObservatoryCache(manifest_file='/home/elijahc/dev/tools/allen-assistant/boc/manifest.json')

exps = boc.get_ophys_experiments(
    imaging_depths=[175],
    targeted_structures=['VISp'],
    cre_lines=['Cux2-CreERT2'],
    stimuli=['natural_scenes'])

In [110]:
import scipy.stats as stats
from allensdk.brain_observatory.dff import movingaverage, movingmode_fast
exp_id = exps[2]['id']
data_set = boc.get_ophys_experiment_data(exp_id)
cids = data_set.get_cell_specimen_ids()
num_cells=50
print('%d Cells in Experiment %d'%(len(cids),exp_id))
idxs = data_set.get_spontaneous_activity_stimulus_table()
#idxs = data_set.get_stimulus_table('natural_scenes')

#t,ftr = data_set.get_corrected_fluorescence_traces(cell_specimen_ids=cids[0:100])
t,ftr = data_set.get_dff_traces(cell_specimen_ids=cids[0:num_cells])

t = t[idxs.start.item():idxs.end.item()]
ftr_crop = ftr[:,idxs.start.item():idxs.end.item()]+1

dt = t - np.roll(t,1)


242 Cells in Experiment 510705057


In [120]:
net = NeuralNetwork(N=3000,dt=0.03318,num_fits=num_cells)
sim = Simulation(network=net,dt=0.03318)
zt = []
rPrt = []
dwt = []
#pretrain_steps= 600
train_steps = 7000
test_steps = 1000
#ft0 = np.repeat(ftr_crop[:,:1],pretrain_steps,axis=1)
#ft_cat = np.concatenate([ft0,ftr_crop],axis=1)

for i in tqdm_notebook(
    sim.iter(steps=train_steps,ft=ftr_crop,train=True),
    total=train_steps,desc='Training'):
    zt.append(sim.network.z)
    if i > 1:
        rPrt.append(sim.network.rPr)
        dwt.append(np.power(sim.network.dw,2).sum())

#for epoch in np.arange(1):
    #for i in tqdm_notebook(
        #sim.iter(steps=train_steps,ft=ftr_crop,train=True),
        #total=train_steps,desc='Training',postfix={'dw':dwt[-1]}):
        #rPrt.append(sim.network.rPr)
        #dwt.append(np.power(sim.network.dw,2).sum())

    
for i in tqdm_notebook(
    sim.iter(steps=test_steps,ft=ftr_crop[:,train_steps:],train=False),
    total=test_steps,desc='Predicting'):
    
    zt.append(sim.network.z)        
    dwt.append(np.power(sim.network.dw,2).sum())
zt = np.squeeze(np.array(zt))
rPrt = np.squeeze(np.array(rPrt))
dwt = np.squeeze(np.array(dwt))


#iplot([{'y':rPrt}])
iplot([
    {'y':dwt,'name':'dw'},
    #{'y':rPrt,'name':'rPr'}
])

In [124]:
pcorr = []
fevs = []
for i in np.arange(num_cells):
    f,z = sim.ft[i,:test_steps],zt[train_steps:,i]
    R,_ = stats.pearsonr(f,z)
    pcorr.append(R)
    
    se = np.power((f-z),2)
    fevs.append(1-(se.mean()/np.var(f)))

df_layout = Layout(
    title='Force Layout Default Title',
    xaxis=dict(
        title='Time(s)',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    yaxis=dict(
        title='dF/F (a.u.)',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
)

pcorr_layout = Layout(
    title='Pearson Corr. Coef. by Cell',
    xaxis=dict(
        title='Cell idx',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    yaxis=dict(
        title='Pearson Corr. Coef. (R)',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
)
d = Bar(y=pcorr)
fig = Figure(data=[d],layout=pcorr_layout)
print(np.mean(pcorr))
iplot(fig)
iplot([{'y':fevs}])
idx=43
iplot([{'x':t,'y':ftr_crop[idx,:]},
       {'x':t[:train_steps],'y':zt[:train_steps,idx]},
      {'x':t[train_steps:],'y':zt[train_steps:,idx]}])

0.02668699436


In [122]:
idx=np.argmin(fevs)
data=[{'x':t,'y':ftr_crop[idx,:],'name':'True f(t)'},
       {'x':t[:train_steps],'y':zt[:train_steps,idx],'name':'Train z(t)'},
      {'x':t[train_steps:],'y':zt[train_steps:,idx],'name':'Test z(t)'}]
df_layout.title='Least Correlated'
worse_fig = Figure(data=data,layout=df_layout)
print(fevs[idx])
iplot(worse_fig)

-1518.48869261


In [123]:
idx=np.argmax(fevs)
best_dat=[{'x':t,'y':ftr_crop[idx,:],'name':'True f(t)'},
       {'x':t[:train_steps],'y':zt[:train_steps,idx],'name':'Train z(t)'},
      {'x':t[train_steps:],'y':zt[train_steps:,idx],'name':'Test z(t)'}]
df_layout.title='Most Correlated'
best_fig = Figure(data=best_dat,layout=df_layout)
print(fevs[idx])
iplot(best_fig)

-4.85008393106


In [17]:
idx=76
best_dat=[{'x':t,'y':ftr_crop[idx,:],'name':'True f(t)'},
       {'x':t[:train_steps],'y':zt[:train_steps,idx],'name':'Train z(t)'},
      {'x':t[train_steps:],'y':zt[train_steps:,idx],'name':'Test z(t)'}]
df_layout.title='Example'
best_fig = Figure(data=best_dat,layout=df_layout)
iplot(best_fig)

IndexError: index 76 is out of bounds for axis 0 with size 50

In [85]:
dxcm,dxtim = data_set.get_running_speed()
dxcm = dxcm[idxs.start.item():idxs.end.item()]
iplot([{'y':dxcm}])